In [ ]:
import numpy as np
import math
s
import collections
import itertools
from io import StringIO

# Apprentissage non supervisé d'un dictionnaire de traduction

Dans ce TP, nous allons nous tenter de construire un dictionnaire de traduction Français-Anglais à partir d'un corpus de traductions alignés,
c'est-à-dire un corpus contenant des couples de phrases : une phrase dans une langue sources (ici le Français) et sa traduction dans une langue cible (ici l'anglais).

L'objectif est de pouvoir contruire une table comme ci-dessous :

| Français | Anglais |
| :- | :- |
| cuisine | cooks, cook, cooking, kitchen, food... |
| comprendre | understand, understood, understanding, realize, ... |
| être | human, being, be, ... |
| économie | free-market, Economy, economics, market, economy, ... |

Nous allons faire de manière non supervisé, c'est-à-dire sans utiliser d'information (c'est-à-dire d'exemples) explicite sur les sorties attendues.
Pour cela, nous allons utiliser un méthode statistique fondée sur des motivations linguistiques.

En linguistique, l'hypothèse distributionnelle défini la sémantique d'un mot de la façon suivant :
le sens d'un mot peut être déduit de son contexte (pour prendre une illustration simple : si deux mots sont synonymes, alors ils seront utilisés dans les mêmes contextes).
Dans le cas bilingue, qui nous intéresse ici,
nous pouvons reformuler cette hypothèse de la façon suivante :
un mot Français et un mot Anglais qui co-occurrent souvent (c'est-à-dire qu'ils apparaissent conjointement dans la phrase source et la traduction cible) sont probablement des traductions.
Par exemple, en analysant les traductions ci-dessous,
on peut rapidement conclure que "cuisine" se traduit en anglais soit pas "kitchen" soit par "cooking" :

| Français | Anglais |
| :- | :- |
| Vivant seul, la **cuisine** de ma mère me manque. | Living on my own, I really miss my Mom’s **cooking****. |
| Elle quitta la **cuisine** avec la bouilloire. | She left the **kitchen** with the kettle boiling. |
| Y a-t-il encore du café dans la **cuisine** ? | Is there any coffee in the **kitchen**? |
| La **cuisine** c’est de famille. | **Cooking** runs in my family. |
| Garçons et filles devraient suivre des cours de **cuisine** à l’école. | Both boys and girls should take **cooking** class in school. |

Nous pouvons faire cette extraction de façon non supervisé.
Vous pouvez tentez de le faire dans l'exemple ci-dessous (qui n'a de sens que si vous **ne parlez pas** le Grec !) :
pouvez vous déduire quelles sont les traductions de "maison" et de "Elli" en Grec ?

| Français | Grec |
| :- | :- |
| Je vais chez nous (lit. dans notre maison).| Πάω στο σπίτι μας. |
| Ma maison est grande| Το σπίτι μου είναι μεγάλο. |
| La maison d’Elli est à côté de la plage.| Το σπίτι της 'Ελλης είναι κοντά στην παραλία. |
| Je m’appelle Elli.| Με λένε 'Ελλη. |
| Une maison du village a brûlé.| 'Ενα σπίτι του χωριού κάηκε |
| J’aime Elli. | Αγαπώ την 'Ελλη. |


## 1. Comptage à partir d'un fichier

Pour compter les (co-)occurrences de mots, nous allons utiliser des objets de type Counter, que nous avons déjà vu lors du TP 1: https://docs.python.org/3/library/collections.html#counter-objects

In [ ]:
counts = collections.Counter()  # création d'un compteur
counts["the"] += 1  # ajoute une occurrence pour le mot "the"

# Ajoute une occurrence pour chaque mot de la liste
# Attention : comme "dog" apparait 2 fois, son compteur sera également incrémenté 2 fois
counts.update(["the", "dog", "is", "a", "dog"])

# Attention : les chaines de caractères sont des itérables,
# donc l'instruction suivante n'émet pas d'erreur,
# mais elle n'incrémentera pas le compteur associé à "an" :
# en effet, cela va incrémenter les compteurs associés aux mots (d'un seul caractère) "a" et "n"
counts.update("an")

# Affiche l'état du compteur
print(counts)

print("\n----\n")

# Il est aussi possible de récupérer les deux mots les plus fréquents
print(counts.most_common(2))

Les fichiers de corpus contiennent une phrase par ligne.
Les phrases sont "tokenisées", c'est à dire qu'il y a un espace entre chaque mot.
Par exemple la phrase "L'Italie, je crois." y sera inscrit comme "L' Italie , je crois .", ce qui permet de facilement récupérer les mots sous la forme d'une liste grâce à la fonction split.

Comparez les deux instructions suivantes :

In [ ]:
txt1 = "L'italie, je crois."
print(txt1.split())

txt2 = "L' italie , je crois ."
print(txt2.split())

L'exemple ci-dessous compte le nombre d'occurrence des mots d'un corpus (dans une seule langue).
Détail important : si un mot apparait 2 fois ou plus dans la même phrase, on ne veut le compter qu'une fois !

In [ ]:
# L'argument instream est un "canal de lecture",
# c'est à dire qu'on peut lire son contenu facilement.
# Ci-dessous, on le lit ligne par ligne
# (un peu comme un parcours d'une liste avec une boucle for)
def count_sentences_with_word(instream):
    counter = collections.Counter()
    for line in instream:
        # enlève les espaces en début et fin de ligne, incluant les retours à la ligne
        # https://docs.python.org/3/library/stdtypes.html#str.strip
        line = line.strip()
        
        # récupère les mots dans la ligne sous forme de liste
        tokens = line.split()
        
        # on ne veut compter chaque mot qu'une fois, même s'il apparait deux fois dans la liste...
        # on peut faire ça facilement : transformer la liste en un ensemble !
        tokens = set(tokens)
        
        for t in tokens:
            counter[t] += 1
            
    return counter

In [ ]:
# Une fonction pour tester le code ci-dessous
def test_count_sentences_with_word():
    # On utilise un objet de type StringIO qui simule un fichier ouvert en lecture (un stream)
    input = StringIO("""a b c
d c a""")
    assert count_sentences_with_word(input) == {'a': 2, 'c': 2, 'b': 1, 'd': 1}

test_count_sentences_with_word()

On peut maintenant utiliser cette fonction pour compter les nombres d'occurrences de tous les mots dans un fichier.
Pour cela, nous avons besoin d'ouvrir le fichier en lecture et de passer son "stream/canal" à la fonction
que l'on a défini ci-dessous.

Qu'observez-vous au niveau des 10 mots les plus courants ?

In [ ]:
with open("./french.corpus") as instream:
    # à l'intérieur de ce bloc (indenté),
    # le fichier est ouvert en lecture,
    # instream est un stream de lecture
    # (que vous pouvez parcourir comme une liste, ce que fait la fonction)
    src_counts = count_sentences_with_word(instream)
    
# récupère les 10 mots les plus fréquents dans le fichier
for word, occurrences in src_counts.most_common(10):
    print("Word \"%s\" appears in %i sentence(s)." % (word, occurrences))

## 2. Construction d'un table de co-occurrence

Nous allons maintenant construire une table de co-occurrences, c'est-à-dire qui compte combien de fois un mot en Français co-occurre avec un autre mot en anglais dans le corpus.
Par exemple, si le corpus contient les deux phrases parallèles suivantes :

- Français : le chien mange
- Anglais : the dog is eating

Nous devons ajouter une co-occurrence de "le" avec les mots "the", "dog", "is" et "eating",
et répéter cette opération pour tous les autres mots.

Pour faire cela, les clés de notre table de co-occurrence seront des couples de mots français/anglais.

In [ ]:
# example de compteur dont les clés sont des couples
# (il y faudrait aussi incrémenter les clés corresponds à tous les autres couples
# de mot français/anglais dans l'exemple)
counter = collections.Counter()

counter[("chien", "the")] += 1
counter[("chien", "dog")] += 1
counter[("chien", "is")] += 1
counter[("chien", "eating")] += 1

print(counter)

Pour itérer en même temps sur les phrases de la langue source et les phrases de la langue cible, vous devez utiliser la fonction zip : https://docs.python.org/3.3/library/functions.html#zip

Comparez les deux boucles ci-dessous pour bien comprendre.

In [ ]:
l1 = ["a", "b", "c"]
l2 = [10, 20, 30]

for i in range(len(l1)):
    e1 = l1[i]
    e2 = l2[i]
    print(e1, e2)

In [ ]:
l1 = ["a", "b", "c"]
l2 = [10, 20, 30]

for e1, e2 in zip(l1, l2):
    print(e1, e2)

Pour implémenter la fonction suivante qui fait ce comptage de co-occurrences, vous devez faire :

1. une boucle avec un zip pour récupérer chaque couple de phrases français/anglais
2. à l'intérieur de celle-ci, une boucle sur les mots de la phrase en français
3. à l'intérieur de cette seconde boucle, une 3ème boucle sur les mots en anglais dans laquelle vous incrémentez le compteur pour tous les couples de mots

Attention : n'oubliez pas que si un mot apparait 2 fois dans une même phrase, il ne doit être compté qu'une fois pour la construction des co-occurrences ! Donc 

- utilisez .strip() pour supprimmer les espaces en début/fin de ligne
- utilisez .split() pour décomposer les phrases en liste de mots
- transformer le résultat en un ensemble pour avoir l'ensemble des mots plutôt que la liste des mots

In [ ]:
def build_cooc_table(src_instream, tgt_instream):
    cooc_table = collections.Counter()
    
    # TODO TODO TODO

Test votre fonction avec le code ci-dessous (si pas d'erreur, c'est que tout fonctionne correctement !)

In [ ]:
def test_build_cooc_table():

    src = StringIO(""" a b c a
d c a
""")
    tgt = StringIO("""A B C A
D C A
""")

    res = build_cooc_table(src, tgt)
    expected_res = {('c', 'C'): 2,
                    ('c', 'A'): 2,
                    ('a', 'C'): 2,
                    ('a', 'A'): 2,
                    ('c', 'B'): 1,
                    ('b', 'B'): 1,
                    ('b', 'C'): 1,
                    ('b', 'A'): 1,
                    ('a', 'B'): 1,
                    ('c', 'D'): 1,
                    ('a', 'D'): 1,
                    ('d', 'A'): 1,
                    ('d', 'D'): 1,
                    ('d', 'C'): 1}

    assert res == expected_res

test_build_cooc_table()

### 3. Construction d'un dictionnaire de traduction : la méthode naïve

On construit maintenant la table de co-occurrences et on affiche les 100 plus fréquentes.

Qu'observez-vous ? Est-ce utile ?

In [ ]:
with open("./french.corpus") as src_instream:
    with open("./english.corpus") as tgt_instream:
        cooc = build_cooc_table(src_instream, tgt_instream)

cooc.most_common(100)

In [ ]:
# on peut aussi le faire avec un seul with
with open("./french.corpus") as src_instream, open("./english.corpus") as tgt_instream:
    cooc = build_cooc_table(src_instream, tgt_instream)
    
cooc.most_common(100)

### 4. Information mutuelle

Nous allons maintenant utiliser l'information mutuelle pour détecter quels sont les couples de mots français/anglais statistiquement dépendant.

Pour cela, nous allons introduire des variables aléatoires de forme X(a) et Y(b), où a est un mot dans la langue source et Y(b) un mot dans la langue cible :

- P(X(a) = 1) : probabilité que le mot a **soit** observé dans la phrase en langue source
- P(X(a) = 0) : probabilité que le mot a **ne soit pas** observé dans la phrase en langue cible
- P(Y(b) = 1) : probabilité que le mot b **soit** observé dans la phrase en langue source
- P(Y(b) = 0) : probabilité que le mot b **ne soit pas** observé dans la phrase en langue cible

À noter que la distribution P(X(a)) est suit une loi de Bernoulli (et de même pour Y(b)).

De la même façon, nous pouvons définir la distribution jointe P(X(a), Y(b)).


**Estimation des distributions marginales**

Nous allons commencer par faire une fonction qui estime la distribution marginal d'un mot. C'est relativement simple :

- $P(X(a) = 1)$ doit être égale à la fréquence d'apparition de m dans le corpus en français, c'est-à-dire le nombre de phrases où $a$ apparait divisé par le nombre total de phrases.
- $P(X(a) = 0) = 1 - P(X(a) = 1)$

La fonction ci-dessous doit retourner un array numpy tel que si p = compute_marginal_distribution(4, 10) :

- p[0] est égal à l'estimation de P(X(a) = 0), soit 0.6 ici
- p[1] est égal à l'estimation de P(X(a) = 1), soit 0.4 ici

(on pourrait représenter cette distribution avec un unique paramètre $\mu$ car c'est une Bernoulli, mais le faire avec un tableau de 2 valeurs simplifiera la suite)

In [ ]:
def compute_marginal_distribution(occurrences, total):
    # TODO TODO TODO

In [ ]:
# test de la fonction ci-dessus

assert type(compute_marginal_distribution(4, 10)) == np.ndarray

assert compute_marginal_distribution(4, 10).shape == (2,)

assert np.allclose(compute_marginal_distribution(4, 10), np.array([0.6, 0.4]))

assert np.allclose(compute_marginal_distribution(10, 10), np.array([0., 1.]))

assert np.allclose(compute_marginal_distribution(0, 10), np.array([1., 0.]))

Nous allons maintenant créer une fonction qui permet de représenter la distribution jointe.
Le tableau doit être de taille 2x2 et contenir les valeurs suivantes :

```
+----------------------+------------------------+
|P(X(a) = 0, Y(b) = 0) | P(X(a) = 0, Y(b) = 1)  |
+----------------------+------------------------+
|P(X(a) = 1, Y(b) = 0) | P(X(a) = 1, Y(b) = 1)  |
+----------------------+------------------------+
```

Vous devez estimer ces probabilités à partir des valeurs suivantes :

- n_a : nombre de phrases où le mot "a" apparait dans les phrases sources du corpus
- n_b : nombre de phrases où le mot "b" apparait dans les phrases cibles du corpus
- n_ab : nombre de phrases où les mot "a" et "b" apparaissent conjointement dans les phrases sources et cibles du corpus
- n : nombre de phrases dans une langue dans le corpus

In [ ]:
def compute_joint_distribution(n_a, n_b, n_ab, n):
    # TODO TODO TODO

In [ ]:
# test de la fonction ci-dessus

assert type(compute_joint_distribution(4, 8, 3, 10)) == np.ndarray

assert compute_joint_distribution(4, 8, 3, 10).shape == (2, 2)

assert np.allclose(compute_joint_distribution(4, 8, 3, 10), np.array([[0.1, 0.5], [0.1, 0.3]]))


On va maintenant implémenter la fonction qui calcule l'information mutuelle.
On a besoin de 3 paramètres, qui sont des distributions :

- joint : paramètres de la distribution jointe P(X(a), Y(b))
- marginal1 : paramètres de la distribution marginale P(X(a))
- marginal2 : paramètres de la distribution marginale P(Y(b))

Ce seront en pratique les tableaux créés par les deux fonctions ci-dessus !

**Attention aux cas particuliers :**
il faut faire attention à ce qu'on calcul.
Faites deux boucles imbriquées, qui itèrent sur les valeurs possibles pour les variables aléatoires X(a) et Y(b).
Lorsque P(X(a) = x, Y(b) = y) = 0 (ou proche de zéro, discons une valeur inférieur à 10e-5),
il risque d'y avoir une erreur dans le calcul du log !
On peut facilement éviter ce problème en ne calculant pas le log, car $0 \log c = 0$, peut importe la valeur de $c$.
Utiliser une condition if/else pour traiter ce cas particulier à part.

In [ ]:
def mutual_information(joint, marginal1, marginal2):
    # TODO TODO TODO

In [ ]:
# Test la fonction ci-dessus

joint = compute_joint_distribution(4, 8, 3, 10)
m1 = compute_marginal_distribution(4, 10)
m2 = compute_marginal_distribution(8, 10)

mi = mutual_information(joint, m1, m2)

assert np.isclose(mi, 0.005131640370881738)

On peut enfin tout combiner ensemble !

Dans l'ordre :

1. construction des dictionnaires de comptage de co-occurrence
2. construction des dictionnaires qui contiennent les distributions marginales et la distribution jointe plutôt que les comptages brutes
3. pour chaque couple de mots (a, b), on calcule l'information mutuelle I(X(a), X(b))
4. on affiche les 100 mots avec les informations mutuelles les plus élevées

In [ ]:
mi = {
    ("maison", "house"): 10.,
    ("maison", "car"): 0.15,
    ("chien", "rouge"): 0.4,
    ("chien", "dog"): 12.5,
}

# Affiche les 2 éléments du dictionnaires dont la valeurs sont les plus élevées.
# Pour votre code ci-dessous, il faudra plutôt afficher les 100 éléments avec les informations mutuelles les plus élevées.
sorted(mi.items(), key=lambda i: i[1], reverse=True)[:2]

In [ ]:
# compte le nombre de phrase dans le corpus,
# pas top mais bon c'est pas grave !

n = 0
with open("./english.corpus") as instream:
    for _ in instream:
        n += 1

#####################
# 1. construction des dictionnaires de comptage de co-occurrence
#####################

# contruit la table de co-occurrence
with open("./french.corpus") as src_instream, open("./english.corpus") as tgt_instream:
    cooc = build_cooc_table(src_instream, tgt_instream)

# comptage du nombre d'apparition de chaque mot dans le corpus
with open("./french.corpus") as src_instream:
    src_counts = count_sentences_with_word(src_instream)

with open("./english.corpus") as tgt_instream:
    tgt_counts = count_sentences_with_word(tgt_instream)

    

In [ ]:
#####################
# 2. construction des dictionnaires qui contiennent les distributions marginales et la distribution jointe plutôt que les comptages brutes
#####################


# clé : un mot en français
# valeure : sa distribution de probabilité d'apparaitre dans une phrase
src_marginal_probabilities = dict()

# clé : un mot en anglais
# valeure : sa distribution de probabilité d'apparaitre dans une phrase
tgt_marginal_probabilities = dict()

# clé : couple (mot français, mot valeur)
# valeure : leur distribution jointe
joint_probabilities = dict()


In [ ]:
#####################
# 3. pour chaque couple de mots (a, b), on calcule l'information mutuelle I(X(a), X(b))
#####################

# clé : couple (mot français, mot valeur)
# valeure : leur information mutuelle
mi = dict()

In [ ]:
#####################
# 4. on affiche les 100 mots avec les informations mutuelles les plus élevées
#####################

sorted(mi.items(), key=lambda i: i[1], reverse=True)[:100]